In [1]:
import torch 
from torch import nn

import ray
from ray.rllib.agents import ppo
from ray.rllib.models import ModelCatalog
from ray.rllib.models.torch.torch_modelv2 import TorchModelV2
from ray.rllib.utils.annotations import override

#from models import VisualEncoder
from train import *
from wrappers_2 import *

/root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
  warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


In [2]:
class VisualEncoder(nn.Module):
    def __init__(self):
        super().__init__()

        self.cnn = nn.Sequential(
            nn.Conv2d(3, 32, kernel_size=2, stride=2, padding=0),  
            nn.ELU(),
            nn.Conv2d(32, 32, kernel_size=2, stride=2, padding=0), 
            nn.ELU(),
            nn.Conv2d(32, 64, kernel_size=2, stride=2, padding=0), 
            nn.ELU(),
            nn.Conv2d(64, 128, kernel_size=2, stride=2, padding=0),
            nn.ELU(), 
            nn.Conv2d(128, 256, kernel_size=2, stride=2, padding=0),
            nn.ELU(),
            nn.Conv2d(256, 512, kernel_size=2, stride=2, padding=0),
            nn.ELU(),
            nn.Flatten(),
        )

    def forward(self, x):
        return self.cnn(x)

In [3]:
class MyModelClass(TorchModelV2, nn.Module):
    def __init__(self, obs_space, action_space, num_outputs, model_config, name):
        TorchModelV2.__init__(self, obs_space, action_space, num_outputs, model_config, name)
        nn.Module.__init__(self)
        features_dim = 512
        self.encoder = VisualEncoder()
        self.encoder.load_state_dict(
            torch.load("/IGLU-Minecraft/models/AngelaCNN/encoder_weigths.pth", map_location=torch.device('cpu'))
        )
        self.mlp = nn.Sequential(
            nn.Linear(features_dim, 256),
            nn.ELU(),
            nn.Linear(256, 256),
            nn.ELU(),
            nn.Linear(256, 256),
            nn.ELU(),
            #nn.Linear(256, 256),
            #nn.ELU(),
            #nn.Linear(256, 256),
            #nn.ELU(),
        )
        self.action_head = nn.Linear(256, action_space.n)
        self.value_head = nn.Linear(256, 1)
        self.last_value = None
        
        self.use_cuda = torch.cuda.is_available()
        if self.use_cuda:
            self.encoder.cuda()
            self.mlp.cuda()
            self.action_head.cuda()
            self.value_head.cuda()
        
    @override(TorchModelV2)
    def forward(self, input_dict, state, seq_lens):
        obs = input_dict['obs'].permute(0, 3, 1, 2).float() / 255.0
        if self.use_cuda:
            obs.cuda()
        
        #with torch.no_grad():
        features = self.encoder(obs)
        features = self.mlp(features)
        action = self.action_head(features)
        self.last_value = self.value_head(features).squeeze(1)
        return action, state
    
    @override(TorchModelV2)
    def value_function(self):
        assert self.last_value is not None, "must call forward() first"
        return self.last_value

In [4]:
ModelCatalog.register_custom_model("my_torch_model", MyModelClass)

In [5]:
import os
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"   # see issue #152
os.environ["CUDA_VISIBLE_DEVICES"]="0"

class RewardWrapper(gym.RewardWrapper):
    def __init__(self, env):
        super().__init__(env)
    
    def reward(self, rew):
        if rew == 0:
            rew = -0.01
        return rew
    
def env_creator(env_config):
    env = gym.make('IGLUSilentBuilder-v0', max_steps=1000)
    env.update_taskset(TaskSet(preset=['C32']))
    env = PovOnlyWrapper(env)
    env = SelectAndPlace(env)
    env = Discretization(env, flat_action_space('human-level'))
    env = RewardWrapper(env)
    return env

from ray.tune.registry import register_env
register_env("my_env", env_creator)

from ray import tune
from ray.rllib.agents.ppo import PPOTrainer

In [6]:
from ray.tune.integration.wandb import WandbLogger

analysis = tune.run(PPOTrainer, 
         config={
             "env": "my_env", 
             "framework": "torch",
             "num_gpus": 1,
             "num_workers": 1,
             "sgd_minibatch_size": 256,
             "clip_param": 0.2,
             "entropy_coeff": 0.01,
             "lambda": 0.95,
             "train_batch_size": 1000,
             #"gamma": 0.99,
             "model": {
                    # Specify our custom model from above.
                    "custom_model": "my_torch_model",
                    # Extra kwargs to be passed to your model's c'tor.
                    "custom_model_config": {},
              },
             "logger_config": {
                  "wandb": {
                      "project": "IGLU-Minecraft",
                      "name":  "PPO C32 pretrained (AngelaCNN + MLP) (3 noops after placement) r: -0.01"
                  }
              }

        },
        loggers=[WandbLogger],
        checkpoint_at_end=True)

/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/_private/services.py:238: UserWarning: Not all Ray Dashboard dependencies were found. To use the dashboard please install Ray using `pip install ray[default]`. To disable this message, set RAY_DISABLE_IMPORT_WARNING env var to '1'.
  warnings.warn(warning_message)
2021-10-24 16:30:32,741	INFO wandb.py:170 -- Already logged into W&B.
2021-10-24 16:30:32,787	ERROR syncer.py:72 -- Log sync requires rsync to be installed.


wandb: Currently logged in as: linar (use `wandb login --relogin` to force relogin)
wandb: WARNING Tried to auto resume run with id 4b4a2_00000 but id b550d_00000 is set.
wandb: wandb version 0.12.5 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade
(pid=149717) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=149717)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))


(pid=149717) 2021-10-24 16:30:36,726	INFO ppo.py:159 -- In multi-agent mode, policies will be optimized sequentially by the multi-GPU optimizer. Consider setting simple_optimizer=True if this doesn't work for you.
(pid=149717) 2021-10-24 16:30:36,727	INFO trainer.py:728 -- Current log_level is WARN. For more information, set 'log_level': 'INFO' / 'DEBUG' or use the -v and -vv flags.
(pid=149722) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=149722)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))
(pid=149717) 2021-10-24 16:30:43,018	WARNING util.py:55 -- Install gputil for GPU system monitoring.
(pid=149722) /root/miniconda/envs/py37/lib/python3.7/site-packages/gym/logger.py:30: UserWarning: WARN: Box bound precision lowered by casting to float32
(pid=149722)   warnings.warn(colorize('%s: %s'%('WARN', msg % args), 'yellow'))
(pid=149722) /root/miniconda/envs/py37/lib/py

Result for PPO_my_env_b550d_00000:
  agent_timesteps_total: 1000
  custom_metrics: {}
  date: 2021-10-24_16-32-05
  done: false
  episode_len_mean: 389.0
  episode_media: {}
  episode_reward_max: -3.789999999999963
  episode_reward_mean: -9.17999999999996
  episode_reward_min: -14.569999999999958
  episodes_this_iter: 2
  episodes_total: 2
  experiment_id: 247f30f7b9bf49cfaf16e302aa75cae8
  hostname: 0b59607b37d7
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.19999999999999996
          cur_lr: 5.000000000000001e-05
          entropy: 2.8745014508565268
          entropy_coeff: 0.009999999999999998
          kl: 0.006464067955185766
          policy_loss: 0.04833170341120826
          total_loss: 0.32310654123624166
          vf_explained_var: -0.14939051866531372
          vf_loss: 0.3022270370481743
    num_agent_steps_sampled: 1000
    num_agent_steps_trained: 1000
    num_steps_sampled: 1000
    num_steps_trained: 1000
  iterations_since

Result for PPO_my_env_b550d_00000:
  agent_timesteps_total: 2000
  custom_metrics: {}
  date: 2021-10-24_16-32-37
  done: false
  episode_len_mean: 395.4
  episode_media: {}
  episode_reward_max: -3.789999999999963
  episode_reward_mean: -6.917999999999961
  episode_reward_min: -14.569999999999958
  episodes_this_iter: 3
  episodes_total: 5
  experiment_id: 247f30f7b9bf49cfaf16e302aa75cae8
  hostname: 0b59607b37d7
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.19999999999999996
          cur_lr: 5.000000000000001e-05
          entropy: 2.8670531272888184
          entropy_coeff: 0.009999999999999998
          kl: 0.006209202833419816
          policy_loss: -0.0887492399248812
          total_loss: 0.2439622550167971
          vf_explained_var: 0.4182874858379364
          vf_loss: 0.36014018290572697
    num_agent_steps_sampled: 2000
    num_agent_steps_trained: 2000
    num_steps_sampled: 2000
    num_steps_trained: 2000
  iterations_since_

...

Result for PPO_my_env_b550d_00000:
  agent_timesteps_total: 1645000
  custom_metrics: {}
  date: 2021-10-25_12-31-01
  done: false
  episode_len_mean: 254.37
  episode_media: {}
  episode_reward_max: -1.9700000000000015
  episode_reward_mean: -2.5436999999999896
  episode_reward_min: -5.209999999999933
  episodes_this_iter: 4
  episodes_total: 6060
  experiment_id: 247f30f7b9bf49cfaf16e302aa75cae8
  hostname: 0b59607b37d7
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.012631191947041024
          cur_lr: 5.000000000000001e-05
          entropy: 0.9379465255472396
          entropy_coeff: 0.009999999999999998
          kl: 0.0294471602396184
          policy_loss: 0.024241585408647855
          total_loss: 0.029096478472153346
          vf_explained_var: 0.303225040435791
          vf_loss: 0.013862405427628094
    num_agent_steps_sampled: 1645000
    num_agent_steps_trained: 1645000
    num_steps_sampled: 1645000
    num_steps_trained: 16450

Result for PPO_my_env_b550d_00000:
  agent_timesteps_total: 1646000
  custom_metrics: {}
  date: 2021-10-25_12-31-54
  done: false
  episode_len_mean: 253.25
  episode_media: {}
  episode_reward_max: -1.9700000000000015
  episode_reward_mean: -2.5324999999999904
  episode_reward_min: -5.209999999999933
  episodes_this_iter: 4
  episodes_total: 6064
  experiment_id: 247f30f7b9bf49cfaf16e302aa75cae8
  hostname: 0b59607b37d7
  info:
    learner:
      default_policy:
        learner_stats:
          cur_kl_coeff: 0.01894678792056154
          cur_lr: 5.000000000000001e-05
          entropy: 0.726323754257626
          entropy_coeff: 0.009999999999999998
          kl: 0.009218455244083795
          policy_loss: 0.026768711747394668
          total_loss: 0.03353107228047318
          vf_explained_var: 0.2110038548707962
          vf_loss: 0.013850938601212368
    num_agent_steps_sampled: 1646000
    num_agent_steps_trained: 1646000
    num_steps_sampled: 1646000
    num_steps_trained: 16460

2021-10-25 12:32:19,108	WARNING tune.py:519 -- SIGINT received (e.g. via Ctrl+C), ending Ray Tune run. This will try to checkpoint the experiment state one last time. Press CTRL+C one more time (or send SIGINT/SIGKILL/SIGTERM) to skip. 
2021-10-25 12:32:19,109	WARNING tune.py:519 -- SIGINT received (e.g. via Ctrl+C), ending Ray Tune run. This will try to checkpoint the experiment state one last time. Press CTRL+C one more time (or send SIGINT/SIGKILL/SIGTERM) to skip. 
2021-10-25 12:32:19,194	WARNING tune.py:519 -- SIGINT received (e.g. via Ctrl+C), ending Ray Tune run. This will try to checkpoint the experiment state one last time. Press CTRL+C one more time (or send SIGINT/SIGKILL/SIGTERM) to skip. 
Process _WandbLoggingProcess-1:
Traceback (most recent call last):
  File "/root/miniconda/envs/py37/lib/python3.7/multiprocessing/process.py", line 297, in _bootstrap
    self.run()
  File "/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/tune/integration/wandb.py", line 200, in

Traceback (most recent call last):
  File "/root/miniconda/envs/py37/lib/python3.7/site-packages/ipython-7.25.0-py3.7.egg/IPython/core/interactiveshell.py", line 3441, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "/tmp/ipykernel_149613/3884869587.py", line 30, in <module>
    checkpoint_at_end=True)
  File "/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/tune/tune.py", line 532, in run
    runner.step()
  File "/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/tune/trial_runner.py", line 554, in step
    self._process_events(timeout=timeout)  # blocking
  File "/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/tune/trial_runner.py", line 675, in _process_events
    timeout=timeout)  # blocking
  File "/root/miniconda/envs/py37/lib/python3.7/site-packages/ray/tune/ray_trial_executor.py", line 718, in get_next_available_trial
    ready, _ = ray.wait(shuffled_results, timeout=timeout)
  File "/root/miniconda/envs/py37/lib/python3.7/sit

TypeError: object of type 'NoneType' has no len()